In [1]:
import gym
import gym_codegen
import numpy as np
import dqn
from dqn import DQNAgent

import io
import os
import random
import sys


def main():
    print "Creating DQN agent..."

    iters = 20000
    n_goal = 0
    n_goal_all = 0
    time_stamp = 0

    ############################################################
    # print x
    # max_steps = 3
    # actions = ["print", " ", "x"]
    ############################################################

    ############################################################
    # print x+1
    max_steps = 5
    actions = ["print", " ", "x", "+", "1"]
    ############################################################

    ############################################################
    # for x in range(x):
    #  print x
    max_steps = 9
    actions = ["for", " ", "x", "in range(x):\n", "print"]
#     max_steps = 7
#     actions = ["for", " ", "x", "in range(x):\n", " print "]
    # max_steps = 15
    # actions = ["for", " ", "in", "range", "(", "x", ")", ":\n", "print"]
    ############################################################

    ############################################################
    # # for i in range(x,n):
    # #  print i
    # max_steps = 17
    # actions = ["for", " ", "i", "in", "range", "(", "x", ",", "n", ")", ":\n", "print"]
    ############################################################

    agent = DQNAgent(max_steps, actions)
    agent.dqn.initial_exploration = iters*0.8

    results = []
    policy_frozen = False
    wins_file = "wins.txt"
    with io.FileIO(wins_file, "w") as file:
        file.write("Winning codes:\n")

    for iter in range(iters):
        if iter % 10 == 0:
            print "\n::{}::".format(iter)

        if iter == 4300: # 2300:
            policy_frozen = True

        env = gym.make("codegen-v0")
        num = random.randrange(1,10) #(1,100)
        env.my_input = num

        ############################################################
        # print x
        # env.goal = str(num)
        ############################################################

        ############################################################
        # print x+1
        # env.goal = str(num + 1)
        ############################################################

        ############################################################
        # for x in range(x):
        #  print x
        env.goal = str("\n".join([str(i) for i in range(num)]))
        ############################################################

        code = env._reset()
        step_in_episode = 0
        total_score = 0.0
        reward = 0.0
        mystate = []
        my_state_new = []

        while step_in_episode < max_steps:
            state = env.code_index_list[:]
            state += np.zeros([max_steps - len(env.code_index_list), agent.dqn.code_idx_size], dtype=int).tolist()

            if step_in_episode == 0:
                action_idx = agent.start(code, state, policy_frozen)
            else:
                action_idx = agent.act(code, state, reward)

            code, reward, terminal, info = env._step(action_idx, agent.dqn.actions)
            state_prime = env.code_index_list[:]
            state_prime += np.zeros([max_steps - len(env.code_index_list), agent.dqn.code_idx_size], dtype=int).tolist()

            agent.dqn.experience_replay(agent.dqn.time_stamp)
            if step_in_episode == max_steps-1 or terminal:
                agent.dqn.stock_experience(agent.dqn.time_stamp, state, action_idx, reward, state_prime, True)
                if terminal:
                    agent.dqn.goal_idx.append(agent.dqn.time_stamp)
                agent.dqn.time_stamp += 1
            else:
                agent.dqn.stock_experience(agent.dqn.time_stamp, state, action_idx, reward, state_prime, False)

            total_score += reward

            if terminal:
                agent.end(reward)

                n_goal_all +=1
                step_in_episode += 1

                if iters-iter<=100:
                    n_goal +=1

            step_in_episode += 1

        if iter >= 100:
            results = results[1:]
        if reward >= 1:
            print "WIN"
            results.append(1.0)
            with io.FileIO(wins_file, "a") as f:
                f.write("\n=====================\n{}\n=====================\n\n".format(code))
                f.flush()
                os.fsync(f)
        else:
            results.append(0.0)
        total_iters = 100 if iter >= 100 else iter + 1
        
        if iter % 10 == 0:
            print "TOTAL {:.2f}% of wins in last {} iters, sum: {}, total good: {}".format(
                100 * sum(results) / total_iters, total_iters, sum(results), len(agent.dqn.goal_idx))

        if iter == 1 + agent.dqn.initial_exploration:
            print "n_goal_all = ", n_goal_all
            print agent.dqn.goal_idx
#             raw_input()
#         env._render()

    print "n_goal : ", n_goal
    print "epsilon : ", agent.epsilon

if __name__ == "__main__":
    main()

Creating DQN agent...
Prepare Data for pretraining...
:0:
good code: 
print    x   

good code: 
for xprint in range(x):
  x

:10000:
good code: 
for  forx in range(x):
 x

:20000:
good code: 
for  forfor in range(x):
 print

:30000:
:40000:
:50000:
good code: 
for   x in range(x):
 x

good code: 
for  xfor in range(x):
 print

good code: 
for xforprint in range(x):
 print

:60000:
good code: 
for  x  in range(x):
 x

good code: 
for printfor  in range(x):
 x

:70000:
good code: 
for forx in range(x):
  x

good code: 
for  forx in range(x):
 x

:80000:
good code: 
for forxprint in range(x):
 x

:90000:
good code: 
for printx  in range(x):
 x

good code: 
for printforprint in range(x):
 print

:100000:
good code: 
for forprintfor in range(x):
 print

:110000:
:120000:
:130000:
good code: 
for forprint in range(x):
 x 

:140000:
good code: 
for x  in range(x):
  print

:150000:
good code: 
for xfor in range(x):
 x 

good code: 
for x in range(x):
 print x

good code: 
for  printfor in ra

[2017-01-19 20:30:13,010] Making new env: codegen-v0
[2017-01-19 20:30:13,049] Making new env: codegen-v0
[2017-01-19 20:30:13,110] Making new env: codegen-v0
[2017-01-19 20:30:13,166] Making new env: codegen-v0
[2017-01-19 20:30:13,197] Making new env: codegen-v0



::0::
Initializing Codegen Environment...
TOTAL 0.00% of wins in last 1 iters, sum: 0.0, total good: 0
Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
for in range(x):
print in range(x):
 x 

Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
forfor in range(x):
print in range(x):
 x

Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
for print in range(x):
in range(x):
print x

Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
for x printx in range(x):
print



[2017-01-19 20:30:13,222] Making new env: codegen-v0
[2017-01-19 20:30:13,249] Making new env: codegen-v0
[2017-01-19 20:30:13,274] Making new env: codegen-v0
[2017-01-19 20:30:13,304] Making new env: codegen-v0
[2017-01-19 20:30:13,329] Making new env: codegen-v0
[2017-01-19 20:30:13,354] Making new env: codegen-v0
[2017-01-19 20:30:13,378] Making new env: codegen-v0
[2017-01-19 20:30:13,407] Making new env: codegen-v0


Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
print  xin range(x):
forprint in range(x):


Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
print in range(x):
 x print in range(x):


Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
for forprint  in range(x):
 x

Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
forxfor in range(x):
xxprintprint

Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
  in range(x):
in range(x):
in range(x):
in range(x):
 forin range(x):



::10::
Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
for x print forfor 

TOTAL 0.00% of wins in last 11 iters, sum: 0.0, total good: 0
Initializing Codegen Environment...
Code: 

import s

...

[2017-01-19 21:37:44,222] Making new env: codegen-v0


Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
for x in range(x):
 x in range(x):




[2017-01-19 21:37:56,356] Making new env: codegen-v0


Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
forforx in range(x):
 x in range(x):




KeyboardInterrupt: 